In [1]:
from top2vec import Top2Vec
import pandas as pd
import umap
import matplotlib.pyplot as plt
from plot import plot_bokeh
import umap.plot
from bokeh.io import output_file, show, save

In [4]:
import psutil
psutil.virtual_memory()

svmem(total=16618618880, available=9040838656, percent=45.6, used=6214643712, free=7362850816, active=7149703168, inactive=633929728, buffers=270843904, cached=2770280448, shared=1008676864, slab=428580864)

In [2]:
df = pd.read_csv('parsed/corpus/2015.csv', index_col=0, na_filter=False)
docs = df.text.to_list()

In [3]:
# model = Top2Vec(docs, embedding_model='universal-sentence-encoder-multilingual', workers=8)
model = Top2Vec(docs, workers=8)

2021-03-26 10:50:55,084 - top2vec - INFO - Pre-processing documents for training
2021-03-26 10:51:25,651 - top2vec - INFO - Creating joint document/word embedding
2021-03-26 11:27:33,306 - top2vec - INFO - Creating lower dimension embedding of documents
2021-03-26 11:27:57,840 - top2vec - INFO - Finding dense areas of documents
2021-03-26 11:28:00,311 - top2vec - INFO - Finding topics


In [4]:
model.save('/media/marcin/Dane/model/2015-top2vec-doc2vec')

In [4]:
model = Top2Vec.load('/media/marcin/Dane/model/2015-top2vec-doc2vec')

In [5]:
topic_sizes, topic_nums = model.get_topic_sizes()

In [7]:
topic_words, word_scores, topic_nums = model.get_topics()

In [10]:
topic_nums,topic_score,topics_words,word_scores = model.get_documents_topics(df.index.to_list())

In [17]:
with open('/media/marcin/Dane/model/topics-top2vec.txt','w') as f:
    print([' | '.join(x[:5]) for x in topics_words], file=f)


In [9]:
vectors = model._get_document_vectors()

reduced2d = umap.UMAP(n_neighbors=15, n_components=2, metric='cosine', verbose=True).fit_transform(vectors)

UMAP(angular_rp_forest=True, dens_frac=0.0, dens_lambda=0.0, metric='cosine',
     verbose=True)
Construct fuzzy simplicial set
Fri Mar 26 12:28:23 2021 Finding Nearest Neighbors
Fri Mar 26 12:28:23 2021 Building RP forest with 15 trees
Fri Mar 26 12:28:23 2021 NN descent for 15 iterations
	 1  /  15
	 2  /  15
	 3  /  15
	 4  /  15
	 5  /  15
	 6  /  15
	 7  /  15
	 8  /  15
	Stopping threshold met -- exiting after 8 iterations
Fri Mar 26 12:28:28 2021 Finished Nearest Neighbor Search
Fri Mar 26 12:28:28 2021 Construct embedding
	completed  0  /  200 epochs
	completed  20  /  200 epochs
	completed  40  /  200 epochs
	completed  60  /  200 epochs
	completed  80  /  200 epochs
	completed  100  /  200 epochs
	completed  120  /  200 epochs
	completed  140  /  200 epochs
	completed  160  /  200 epochs
	completed  180  /  200 epochs
Fri Mar 26 12:28:47 2021 Finished embedding


In [10]:
df['topic'] = model.doc_top

In [11]:
umap.plot.output_notebook()

Loading BokehJS ...

In [12]:
topic_words_joined = [" | ".join(words[:5]) for words in topic_words]

df['topic_words'] = [topic_words_joined[t] for t in df.topic]
hover_data = df[['posel','topic_words']]
hover_data.reset_index(inplace=True)

In [14]:
p = plot_bokeh(reduced2d, labels=df.topic.to_list(), hover_data=hover_data, point_size=2, width=1200, height=1200, interactive_text_search=True)
# output_file("plots/umap-top2vec-2015.html")
# save(p)
show(p)